In [1]:
import os
import numpy as np
import pickle
import sys
import scipy.stats as stats
from tqdm import tqdm
import matplotlib.pyplot as plt
sys.path.append('../')
from utils import get_distance, haversineDistance
from placecell import PlaceNetwork, loadNetwork
from statsmodels.stats.multitest import multipletests

In [2]:
def one_tailed_t_test(array1, array2, alternative='greater'):
    """
    Perform a one-tailed t-test on two arrays.

    Parameters:
    - array1, array2: The two arrays for which the t-test will be performed.
    - alternative: The direction of the test. It can be 'greater' or 'less'.
    
    Returns:
    - t_statistic: The t-statistic of the test.
    - p_value: The p-value of the test.
    """
    _, p_value = stats.ttest_ind(array1, array2)
    
    if alternative == 'greater':
        t_statistic = p_value / 2  # Divide p-value by 2 for a one-tailed test
    elif alternative == 'less':
        t_statistic = 1 - p_value / 2  # Subtract p-value divided by 2 from 1
    else:
        raise ValueError("Invalid alternative. Use 'greater' or 'less'.")

    result = {
        'statistic': t_statistic,
        'p_value': p_value,
    }
    
    return result

In [3]:
NAIVE_PATH = 'naive_pths.pkl'
RRT_PATH = 'rrt_pths.pkl'
SW_PATH = 'sw_pths.pkl'
ASTAR_PATH = 'astar_pths.pkl'
SW_NAIVE_PATH = 'sw_naive_pths.pkl'

In [4]:
def loadFromFile(file):
    f = open(file, 'rb')
    data = pickle.load(f)
    return data

In [5]:
naive = loadFromFile(NAIVE_PATH)
rrt = loadFromFile(RRT_PATH)
sw = loadFromFile(SW_PATH)
astar = loadFromFile(ASTAR_PATH)
sw_naive = loadFromFile(SW_NAIVE_PATH)

In [6]:
new_sw_naive = []
#Reorder sw_naive
for i in tqdm(astar):
    for j in sw_naive:
        if i[0] == j[0] and i[-1] == j[-1]:
            new_sw_naive.append(j)

100%|████████████████████████████████████████████████████████████████████████████| 57086/57086 [12:07<00:00, 78.45it/s]


In [7]:
sw_naive = new_sw_naive

In [8]:
total = len(naive)
print(f"Total number of paths: {total}")

Total number of paths: 57086


In [9]:
sameasrrt = 0
sameasnaive = 0
sameasastar = 0
for n, r, s, a in zip(naive, rrt, sw, astar):
    if s == a:
        sameasastar += 1     
    if s == n:
        sameasnaive += 1
    if s == r:
        sameasrrt += 1

In [10]:
print(f"SWP and RRT same: {(sameasrrt / total) * 100:.2f}%")
print(f"SWP and naive same: {(sameasnaive / total) * 100:.2f}%")
print(f"SWP and astar same: {(sameasastar / total) * 100:.2f}%")

SWP and RRT same: 12.58%
SWP and naive same: 17.80%
SWP and astar same: 32.97%


In [11]:
same = 0
for a, s in zip(naive, sw_naive):
    if a == s:
        same += 1
    else:
        if len(a) != len(s):
            print("Should not get here: costs should be identical")

print(f"SWP and astar same on empty map: {(same / total) * 100:.2f}%")

SWP and astar same on empty map: 97.41%


In [12]:
network = PlaceNetwork()
data = loadNetwork("../fixed_wgts")
network.loadFromFile(data)

In [13]:
wgts = network.normalizeWeights([0, 1, 4, 5])

In [14]:
def calculateTotalCost(wgts, path):
    reversedpath = path[::-1]
    cost = 0
    for i in range(len(path) - 1):
        cost += wgts[(reversedpath[i], reversedpath[i+1])]
    return cost

def calculateTotalDistance(network, wgts, path):
    reversedpath = path[::-1]
    distance = 0
    for i in range(len(path) - 1):
        d1 = network.cells[path[i]].origin
        d2 = network.cells[path[i+1]].origin
        distance += haversineDistance(d1[0], d1[1], d2[0], d2[1])
    return distance

def distance(network, path):
    d1 = network.cells[path[0]].origin
    d2 = network.cells[path[-1]].origin
    return(haversineDistance(d1[0], d1[1], d2[0], d2[1]))

In [15]:
distances = [distance(network, i) for i in sw]

In [16]:
astarcosts = []
astarci = []

swpcosts = []
swpci = []

naivecosts = []
naiveci = []

rrtcosts = []
rrtci = []

_swtotals = np.array([calculateTotalCost(wgts, i) for i in sw])
_distancessw = np.array([distance(network, i) for i in sw])

_astartotals = np.array([calculateTotalCost(wgts, i) for i in astar])
_distancesastar = np.array([distance(network, i) for i in astar])

_naivetotals = np.array([calculateTotalCost(wgts, i) for i in naive])
_distancesnaive = np.array([distance(network, i) for i in naive])

_rrttotals = np.array([calculateTotalCost(wgts, i) for i in rrt])
_distancesrrt = np.array([distance(network, i) for i in rrt])


def getMeanandCI(costs, distances, d, ci):
    slice = costs[np.array(distances) > d]
    mean = np.mean(slice)
    std_error = np.std(slice, ddof=1) / np.sqrt(len(slice))

    dof = len(slice) - 1
    confidence_interval = stats.norm.interval(ci, loc=mean, scale=std_error)

    return mean, confidence_interval

level=0.99

for d in range(0, 81):
    astarmean, astarconf = getMeanandCI(_astartotals, _distancesastar, d, level)
    swpmean, swpconf = getMeanandCI(_swtotals, _distancessw, d, level)
    naivemean, naiveconf = getMeanandCI(_naivetotals, _distancesnaive, d, level)
    rrtmean, rrtconf = getMeanandCI(_rrttotals, _distancesrrt, d, level)
    
    astarcosts.append(astarmean)
    astarci.append(astarconf)
    
    swpcosts.append(swpmean)
    swpci.append(swpconf)
    
    naivecosts.append(naivemean)
    naiveci.append(naiveconf)
    
    rrtcosts.append(rrtmean)
    rrtci.append(rrtconf)

In [17]:
minimum_distance = 0

#COSTS
swp_costs = [calculateTotalCost(wgts, i) for i in sw if distance(network, i) > minimum_distance]
swp_avg = np.mean(swp_costs)

rrt_costs = [calculateTotalCost(wgts, i) for i in rrt if distance(network, i) > minimum_distance]
rrt_avg = np.mean(rrt_costs)

astar_costs = [calculateTotalCost(wgts, i) for i in astar if distance(network, i) > minimum_distance]
astar_avg = np.mean(astar_costs)

naive_costs = [calculateTotalCost(wgts, i) for i in naive if distance(network, i) > minimum_distance]
naive_avg = np.mean(naive_costs)

#DISTANCES
swp_dist = [calculateTotalDistance(network, wgts, i) for i in sw if distance(network, i) > minimum_distance]
swp_dist_avg = np.mean(swp_costs)

rrt_dist = [calculateTotalDistance(network, wgts, i) for i in rrt if distance(network, i) > minimum_distance]
rrt_avg = np.mean(rrt_costs)

astar_dist = [calculateTotalDistance(network, wgts, i) for i in astar if distance(network, i) > minimum_distance]
astar_dist_avg = np.mean(astar_costs)

naive_dist = [calculateTotalDistance(network, wgts, i) for i in naive if distance(network, i) > minimum_distance]
naive_dist_avg = np.mean(naive_costs)


In [18]:
rrt_result = one_tailed_t_test(swp_costs, rrt_costs, alternative='less')
print(f"Mean swp cost: {np.mean(swp_costs)}")
print(f"Mean rrt cost: {np.mean(rrt_costs)}")
print(f"p-value: {rrt_result['p_value']}")

print("___________________________________________")

astar_result = one_tailed_t_test(swp_costs, astar_costs, alternative='less')
print(f"Mean swp cost: {np.mean(swp_costs)}")
print(f"Mean astar cost: {np.mean(astar_costs)}")
print(f"p-value: {astar_result['p_value']}")

print("___________________________________________")

naive_result = one_tailed_t_test(swp_costs, naive_costs, alternative='less')
print(f"Mean swp cost: {np.mean(swp_costs)}")
print(f"Mean naive cost: {np.mean(naive_costs)}")
print(f"p-value: {naive_result['p_value']}")

Mean swp cost: 19.356654400747683
Mean rrt cost: 22.066295101941122
p-value: 0.0
___________________________________________
Mean swp cost: 19.356654400747683
Mean astar cost: 19.548542238727688
p-value: 0.0002588291659747119
___________________________________________
Mean swp cost: 19.356654400747683
Mean naive cost: 21.845377554361562
p-value: 0.0


In [19]:
all_costs = [i['p_value'] for i in [astar_result, rrt_result, naive_result]]
cost_corr = multipletests(all_costs, alpha=0.05, method='bonferroni')
print("COST (atar, rrt, naive)")
print(cost_corr)

COST (atar, rrt, naive)
(array([ True,  True,  True]), array([0.00077649, 0.        , 0.        ]), 0.016952427508441503, 0.016666666666666666)


In [20]:
rrt_dist_result = one_tailed_t_test(swp_dist, rrt_dist, alternative='less')
print(f"Mean swp distance: {np.mean(swp_dist)}")
print(f"Mean rrt distance: {np.mean(rrt_dist)}")
print(f"p-value: {rrt_dist_result['p_value']}")

print("___________________________________________")

astar_dist_result = one_tailed_t_test(swp_dist, astar_dist, alternative='less')
print(f"Mean swp distance: {np.mean(swp_dist)}")
print(f"Mean astar distance: {np.mean(astar_dist)}")
print(f"p-value: {astar_dist_result['p_value']}")

print("___________________________________________")

naive_dist_result = one_tailed_t_test(swp_dist, naive_dist, alternative='less')
print(f"Mean swp distance: {np.mean(swp_dist)}")
print(f"Mean naive distance: {np.mean(naive_dist)}")
print(f"p-value: {naive_dist_result['p_value']}")

Mean swp distance: 50.910470411071465
Mean rrt distance: 59.00588995741761
p-value: 0.0
___________________________________________
Mean swp distance: 50.910470411071465
Mean astar distance: 51.732074193787376
p-value: 6.499648863252795e-09
___________________________________________
Mean swp distance: 50.910470411071465
Mean naive distance: 47.731018958899746
p-value: 4.152574805279658e-121


In [21]:
all_dist = [i['p_value'] for i in [astar_dist_result, rrt_dist_result, naive_dist_result]]
dist_corr = multipletests(all_dist, alpha=0.05, method='bonferroni')
print("DISTANCE (atar, rrt, naive)")
print(dist_corr)

DISTANCE (atar, rrt, naive)
(array([ True,  True,  True]), array([1.94989466e-008, 0.00000000e+000, 1.24577244e-120]), 0.016952427508441503, 0.016666666666666666)


In [22]:
import matplotlib
matplotlib.rc('font', family='serif')
plt.figure(figsize=(12,12), dpi=900)
plt.xlabel("Minimum path length considered (meters)", fontsize=30)
plt.ylabel("Mean Cost", fontsize=30)


plt.plot(astarcosts, label='Mean A* Cost', color='tab:blue', linewidth=2)
astarlower, astarupper = zip(*astarci)
plt.fill_between(range(len(astarcosts)), astarlower, astarupper, color='tab:blue', alpha=0.2)


plt.plot(swpcosts, label='Mean SWP Cost', color='tab:orange', linewidth=2)
swplower, swpupper = zip(*swpci)
plt.fill_between(range(len(swpcosts)), swplower, swpupper, color='tab:orange', alpha=0.2)

plt.plot(naivecosts, label='Mean Naive Cost', color='tab:green', linewidth=2)
naivelower, naiveupper = zip(*naiveci)
plt.fill_between(range(len(naivecosts)), naivelower, naiveupper, color='tab:green', alpha=0.2)

plt.plot(rrtcosts, label='Mean RRT* Cost', color='tab:red', linewidth=2)
rrtlower, rrtupper = zip(*rrtci)
plt.fill_between(range(len(rrtcosts)), rrtlower, rrtupper, color='tab:red', alpha=0.2)

plt.xticks(fontsize=30)
plt.yticks(fontsize=30)
plt.legend(fontsize=24)
plt.margins(0)
plt.savefig("swp_improvement.pdf")
plt.show()